In [6]:
import os
import re
import gzip
import shutil
from pathlib import Path
import pandas as pd
from IPython.display import display, HTML

In [5]:
def create_scrollable_table(df, table_id, max_height='300px'):
    """
    Displays a pandas DataFrame as a scrollable HTML table.
    
    Args:
        df (pd.DataFrame): The DataFrame to display.
        table_id (str): A unique ID for the HTML table element.
        max_height (str): The maximum height of the scrollable table (e.g., '300px').
    """
    html = f'<div id="{table_id}" style="height:{max_height}; overflow:auto;">'
    html += df.to_html()
    html += '</div>'
    return HTML(html)

In [9]:
# Input and output directories
INPUT_DIR = Path("../data/bse/equity/bse")
OUTPUT_DIR = Path("../data/bse/equity/")

In [3]:
# Pattern to match filenames like 31OCT2024.csv
FILENAME_PATTERN = re.compile(r"(\d{2})([A-Z]{3})(\d{4})\.csv")

In [4]:
def extract_year_from_filename(filename: str) -> str | None:
    """Extracts year from filenames like 31OCT2024.csv"""
    match = FILENAME_PATTERN.match(filename)
    return match.group(3) if match else None

In [5]:
def create_year_folder(year: str) -> Path:
    """Creates and returns the year-wise output folder"""
    year_folder = OUTPUT_DIR / year
    year_folder.mkdir(parents=True, exist_ok=True)
    return year_folder

In [6]:
def compress_csv_to_gz(source_file: Path, dest_folder: Path) -> Path:
    """Compresses the CSV file to .csv.gz and saves it in dest_folder"""
    compressed_filename = source_file.name + ".gz"
    compressed_path = dest_folder / compressed_filename
    with open(source_file, 'rb') as f_in, gzip.open(compressed_path, 'wb') as f_out:
        shutil.copyfileobj(f_in, f_out)
    return compressed_path

In [7]:
def process_file(csv_file: Path):
    """Main logic to process one file: extract year, compress, and move"""
    year = extract_year_from_filename(csv_file.name)
    if not year:
        print(f"Skipping invalid file: {csv_file.name}")
        return

    year_folder = create_year_folder(year)
    compressed_path = compress_csv_to_gz(csv_file, year_folder)
    csv_file.unlink()  # Remove original CSV
    print(f"Compressed and moved: {csv_file.name} → {compressed_path}")

In [ ]:
for csv_file in INPUT_DIR.glob("*.csv"):
        process_file(csv_file)

In [3]:

# Load files (update the path as needed)
df_old = pd.read_csv("~/Downloads/01AUG2025-Old.csv")
df_new = pd.read_csv("~/Downloads/01AUG2025.csv")

# Clean column names
df_old.columns = df_old.columns.str.strip().str.replace('"', '')
df_new.columns = df_new.columns.str.strip().str.replace('"', '')

# Select relevant columns and rename for consistency
df_old_ohlc = df_old[["SYMBOL", "OPEN_PRICE", "HIGH_PRICE", "LOW_PRICE", "CLOSE_PRICE"]].copy()
df_old_ohlc.columns = ["SYMBOL", "OPEN", "HIGH", "LOW", "CLOSE"]

df_new_ohlc = df_new[["TckrSymb", "OpnPric", "HghPric", "LwPric", "ClsPric"]].copy()
df_new_ohlc.columns = ["SYMBOL", "OPEN", "HIGH", "LOW", "CLOSE"]

# Merge on SYMBOL
merged = pd.merge(df_old_ohlc, df_new_ohlc, on="SYMBOL", suffixes=("_OLD", "_NEW"))

# Compare OHLC
for col in ["OPEN", "HIGH", "LOW", "CLOSE"]:
    merged[f"MATCH_{col}"] = merged[f"{col}_OLD"] == merged[f"{col}_NEW"]

# Identify fully matching rows
merged["ALL_MATCH"] = merged[[f"MATCH_{col}" for col in ["OPEN", "HIGH", "LOW", "CLOSE"]]].all(axis=1)

# Display only mismatched rows (optional)
mismatches = merged[~merged["ALL_MATCH"]]

# Show mismatch summary
match_summary = merged["ALL_MATCH"].value_counts()

# Show merged DataFrame (or mismatches only)
print("Match Summary:\n", match_summary)
print("\nMismatched Rows:\n", mismatches.head(20))  # show top 10 mismatches

Match Summary:
 ALL_MATCH
True     2908
False       6
Name: count, dtype: int64

Mismatched Rows:
          SYMBOL  OPEN_OLD  HIGH_OLD  LOW_OLD  CLOSE_OLD  OPEN_NEW  HIGH_NEW  \
855        GAIL    177.67    177.68   173.85     174.39    177.00    177.00   
856        GAIL    177.00    177.00   177.00     174.39    177.67    177.68   
1509     M&MFIN    256.85    261.00   255.80     258.50   2219.10   2219.10   
1510     M&MFIN   2219.10   2219.10  2204.95    2204.95    256.85    261.00   
2067  RADIOCITY      8.85      8.85     8.62       8.67    114.20    114.30   
2068  RADIOCITY    114.20    114.30   114.20     114.20      8.85      8.85   

      LOW_NEW  CLOSE_NEW  MATCH_OPEN  MATCH_HIGH  MATCH_LOW  MATCH_CLOSE  \
855    177.00     174.39       False       False      False         True   
856    173.85     174.39       False       False      False         True   
1509  2204.95    2204.95       False       False      False        False   
1510   255.80     258.50       False       

In [2]:
df = pd.read_csv("~/Downloads/06AUG2025.csv.gz",compression='gzip')

In [7]:
create_scrollable_table(df, 'my_table')